<div>
    <h1> Кредитный скоринг</h1>
</div>

<div class="alert alert-info">
<h2> Комментарий</h2>

Все глобальные комментарии по коду будут сделаны в таком формате
</div>

Импорт нужных библиотек:

In [1]:
import pandas as pd
import numpy as np
import requests
from bs4 import BeautifulSoup
from tqdm import tqdm
import matplotlib.pyplot as plt

import warnings
warnings.filterwarnings("ignore")

# Загрузка датасета

Парсинг датасета с [сайта](http://dataset.website)

In [2]:
url = 'http://dataset.website'
page = requests.get(url)

end = {
    "data":[]
}

soup = BeautifulSoup(page.text, 'html.parser')
table = soup.find('tbody')

for tr in tqdm(table.findAll("tr")):
    tr_prep = [tr.findAll("th")[0].text]
    for td in tr.findAll("td"):
        tr_prep.append(td.text)

    end["data"].append(tr_prep)
df = pd.DataFrame(end['data'])
df.columns = ['Customer_ID', 'Name', 'Age', 'Occupation', 'Num_of_Delayed_Payment', 'Annual_Income', 'Monthly_Inhand_Salary',
              'Num_Bank_Accounts', 'Num_Credit_Card', 'Num_of_Loan', 'Delay_from_due_date',	'Monthly_Balance', 'Outstanding_Debt',
              'Credit_Score']
df

100%|██████████████████████████████████| 10000/10000 [00:00<00:00, 23008.23it/s]


Customer_ID             Name  Age  Occupation Num_of_Delayed_Payment  \
0      CUS_0xd40    Aaron Maashoh   23   Scientist                      7   
1      CUS_0xd40    Aaron Maashoh   23   Scientist                     8_   
2     CUS_0x21b1  Rick Rothackerj  28_     _______                      4   
3     CUS_0x21b1  Rick Rothackerj   28     Teacher                      1   
4     CUS_0x21b1  Rick Rothackerj   28     Teacher                     -1   
...          ...              ...  ...         ...                    ...   
9995  CUS_0xa1bd           Ermanv   41  Journalist                     10   
9996  CUS_0xa1bd           Ermanv   41  Journalist                     12   
9997  CUS_0xa1bd           Ermanv   41     _______                     12   
9998  CUS_0xa1bd           Ermanv   41  Journalist                     14   
9999  CUS_0xa1bd           Ermanv   41  Journalist                     12   

     Annual_Income Monthly_Inhand_Salary Num_Bank_Accounts Num_Credit_Card  \
0         19114.12       1824.8433333333                 3               4   
1         19114.12       1824.8433333333                 3               4   
2         34847.84       3037.9866666667                 2               4   
3         34847.84       3037.9866666667                 2               4   
4        34847.84_       3037.9866666667                 2            1385   
...            ...                   ...               ...             ...   
9995      23437.79       1711.1491666667                 8               4   
9996      23437.79       1711.1491666667                 8               4   
9997      23437.79       1711.1491666667                 8               4   
9998      23437.79       1711.1491666667                 8               4   
9999      23437.79       1711.1491666667                 8               4   

     Num_of_Loan Delay_from_due_date     Monthly_Balance Outstanding_Debt  \
0              4                   3  312.49408867943663           809.98   
1              4                   3   244.5653167062043           809.98   
2              1                   3  470.69062692529184           605.03   
3              1                   7   484.5912142650067           605.03   
4              1                   3  466.46647639764313           605.03   
...          ...                 ...                 ...              ...   
9995           3                  24  320.61940278914057           589.94   
9996           3                  25   328.6262878504154           589.94   
9997           3                  25   328.7174244853496           589.94   
9998           3                  24  244.96479442371486           589.94   
9999           3                  25  240.27220818167982           589.94   

     Credit_Score  
0            Good  
1            Good  
2        Standard  
3            Good  
4        Standard  
...           ...  
9995     Standard  
9996         Poor  
9997         Poor  
9998         Poor  
9999         Poor  

[10000 rows x 14 columns]

In [3]:
columns_start = df.columns
columns_start

Index(['Customer_ID', 'Name', 'Age', 'Occupation', 'Num_of_Delayed_Payment',
       'Annual_Income', 'Monthly_Inhand_Salary', 'Num_Bank_Accounts',
       'Num_Credit_Card', 'Num_of_Loan', 'Delay_from_due_date',
       'Monthly_Balance', 'Outstanding_Debt', 'Credit_Score'],
      dtype='object')

## Пропущенные значения

<div class="alert alert-info">
<h2> Комментарий </h2>

Очень много аномальных значений надо заменять путем группирования пользователей по id и поиска моды в каждой получившейся группе, далее заменить аномалии на моду
</div>

In [4]:
vals = ['Age', 'Num_of_Delayed_Payment', 'Monthly_Inhand_Salary', 'Num_Bank_Accounts', 'Num_Credit_Card', 
        'Num_of_Loan', 'Monthly_Balance', 'Delay_from_due_date', 'Outstanding_Debt', 'Annual_Income']
for val in vals:
    df[val] = pd.to_numeric(df[val], errors='coerce')

In [5]:
df["Age"] = df['Age'].fillna(0)
df['Annual_Income'] = df['Annual_Income'].fillna(0)
df['Num_of_Loan'] = df['Num_of_Loan'].fillna(0).astype('int64')

In [6]:
occupation_group = df.groupby('Customer_ID')['Occupation']
def kill_occupation_nans(row):
    global df
    if row['Occupation'].strip().lower() == '_______':
        idx = row["Customer_ID"]
        d = list(filter(lambda x: x != '_______', df[df['Customer_ID'] == idx]['Occupation'].unique()))[0]
        row['Occupation'] = d
    return row
df = df.apply(kill_occupation_nans, axis=1)

In [7]:
vals = ['Num_Bank_Accounts', 'Num_Credit_Card', 'Num_of_Loan', 
        'Outstanding_Debt', 'Annual_Income', 'Num_of_Delayed_Payment', 'Age']

for val in vals:
    Num_Bank_Accounts_group = df.groupby('Customer_ID')[val]
    for group in Num_Bank_Accounts_group:
        res = group[1].mode()[0]
        df.loc[df['Customer_ID'] == group[0], val] = res

In [8]:
Monthly_Balance_mean = df.loc[df['Customer_ID'] == 'CUS_0x9885', 'Monthly_Balance'].mean()
df['Monthly_Balance'] = df['Monthly_Balance'].fillna(Monthly_Balance_mean)

In [9]:
df.loc[df['Delay_from_due_date'] < 0] = 0

In [10]:
df = df.loc[(0 <= df['Num_of_Loan']) & (df['Num_of_Loan'] <= 9)]

In [11]:
df = df.loc[df['Age'] != 0]

In [12]:
df.loc[df['Age'] > 56] = df["Age"].median()

# __EDA и часть визуализации__

In [25]:
!python -m pip install pandas-profiling
!python -m pip install wordcloud

In [26]:
import pandas as pd
import seaborn as sns
from pandas_profiling import ProfileReport
from wordcloud import WordCloud, STOPWORDS

sns.set_style("darkgrid")

In [27]:
profile = ProfileReport(df)
profile.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

В данном окне с внушительным анализом по всем показателям можем посмотувидеть различные закономерности и ососбенности переменных.

- Так, по анализу переменной __Age__ можем отметить, что клиенты банка в основном люди в возрасте от 20 до 45 лет, при этом средний возраст раемщика __33 года__, минимальный же возраст __14 лет__, максимальный - __56 лет__.


- Больше всего среди всего числа заемщиков представителей профессии __журналист, переводчик и адвокат__.


- __Количество просроченных платежей в среднем составляет 13__, при этом мы видим, что есть и такие клиенты, у которых отстутствуют просроченные платежи. Ниже можно увидеть, что в основном отсутствуют просрочки и людей с Credit Score равным Good и Standard, однако есть и представители плохой кредитоспособности - значит, можно предположить, что __данный показатель не настолько сильно, но все же влияет на оценку кредитоспособности заемщика__.


- Средний годовой доход равен __51032.4 долларов__, средний месячный доход - __4289.5__.


- Среднее количество кредитных карт - __5.5__, и мы наблюдаем всего 6 клиентов, у которых отсутсвуют карты, это значит, что __большинство клиентов являются заемщиками именно по кредитным картам__.


- А вот __среднее количество кредитов меньше, чем среднее количество кредитных карт, всего 3.5__, и нулей гораздо больше, что подтверждает утверждение о том, что большинство клиентов являются заемщиками именно по кредитным картам.


- __Задержки от даты платежа наблюдаются часто__, в среднем составляют 21 день, однако по гистограмме видим, что примерно равномерно распределены от 5 до 32-32 дней, за исключением определенных выделяющихся значений.

- __Ежемесячный баланс__ распределен почти нормально (немного смещен влево и правый хвост больше). Среднее значение - __407 долларов__. 

- Оставшаяся задолженность клиентов в среднем __1405 долларов__, что достаточно небольшая сумма для кредитов, но вполне реальная для кредитных карт. 

- И самый интересный показатель - кредитный рейтинг клиента. Заметим, что чаще у банка заемщики __со стандартным кредитным рейтингом - 5212, с плохим - 2927, а вот с хорошим всего 1724 человека__. 


Числовые показатели довольно сильно розняться взависимости от категории кредитоспособности заемщика, поэтому разделим всех клиентов банка на три группы по кредитному рейтингу и проанализируем данные показатели по ним.

In [28]:
df[df['Num_of_Delayed_Payment'] == 0]['Credit_Score'].value_counts()

Good        101
Standard     99
Poor         43
Name: Credit_Score, dtype: int64

In [29]:
df[df['Num_Bank_Accounts'] == 0]['Credit_Score'].value_counts()

Standard    200
Good        166
Poor        120
Name: Credit_Score, dtype: int64

In [30]:
df["Occupation"] = df[df["Occupation"] != 33.0]["Occupation"]
df.dropna(inplace=True)
df["Occupation"].unique()

array(['Scientist', 'Teacher', 'Engineer', 'Entrepreneur', 'Developer',
       'Lawyer', 'Media_Manager', 'Doctor', 'Journalist', 'Manager',
       'Accountant', 'Musician', 'Mechanic', 'Writer', 'Architect'],
      dtype=object)

In [31]:
text = ' sep '.join(df.sort_values(by='Occupation')['Occupation'].to_list()) 

wordcloud = WordCloud(width = 3000, 
                      height = 2000, 
                      random_state=1, 
                      background_color='LavenderBlush', 
                      margin=20, 
                      colormap='tab10',
                      collocations=True,
                      stopwords = ['sep']).generate(text)

plt.figure(figsize=(13, 6))
plt.imshow(wordcloud) 
plt.axis("off")

(-0.5, 2999.5, 1999.5, -0.5)

In [32]:
corr_matrix = df.corr()

sns.heatmap(df.corr(), cmap='coolwarm', annot=True);

Видим, что наиболее сильная корреляция у таких пар, как :

- ежемесячный и годовой доход клиента (что вполне логично и может не рассматриваться, как важная зависимость)

- количество банковских счетов и количество просроченных платежей 

- Ежемесячный чистый доход и Месячный баланс

- Оставшаяся задолженность и Количество займов, Задержка относительно срока платежа


Посмотрим от каких переменных в наибольшей степени зависит кретинтый рейтинг клиента

In [33]:
credit_score_dict = {'Poor': 0, 'Standard': 1, 'Good': 2}

df['Credit_Score_Num'] = df['Credit_Score'].replace(credit_score_dict)

correlations = df.corr()['Credit_Score_Num'].sort_values(ascending=False)
print('\nMost Positive Correlations:\n','\n', correlations.head(5), '\n')
print('Most Negative Correlations:\n','\n', correlations.tail(5))


Most Positive Correlations:
 
 Credit_Score_Num         1.000000
Monthly_Balance          0.223130
Monthly_Inhand_Salary    0.217677
Annual_Income            0.217396
Age                      0.162957
Name: Credit_Score_Num, dtype: float64 

Most Negative Correlations:
 
 Num_Bank_Accounts     -0.356801
Num_of_Loan           -0.362114
Outstanding_Debt      -0.373486
Num_Credit_Card       -0.388982
Delay_from_due_date   -0.415741
Name: Credit_Score_Num, dtype: float64


Создадим три таблицы с представителями каждой категорией рейтинга клиента.

In [34]:
df.pivot_table(values=['Age','Num_of_Delayed_Payment', 'Annual_Income', 'Monthly_Inhand_Salary', 'Num_Bank_Accounts',
                        'Num_Credit_Card', 'Num_of_Loan', 'Delay_from_due_date', 'Monthly_Balance', 'Outstanding_Debt'], 
               index='Credit_Score', 
               aggfunc=['median'], dropna=True)

median                                                    \
                Age Annual_Income Delay_from_due_date Monthly_Balance   
Credit_Score                                                            
Good           36.0      60781.48                  10      418.101726   
Poor           30.0      34107.42                  26      306.422370   
Standard       33.0      38073.60                  18      344.876175   

                                                                      \
             Monthly_Inhand_Salary Num_Bank_Accounts Num_Credit_Card   
Credit_Score                                                           
Good                   5082.143333                 3               4   
Poor                   2902.990833                 7               6   
Standard               3282.269196                 6               5   

                                                                  
             Num_of_Delayed_Payment Num_of_Loan Outstanding_Debt  
Credit_Score                                                      
Good                            8.0           2           670.05  
Poor                           16.0           5          1843.93  
Standard                       14.0           3          1013.57

In [35]:
df.pivot_table(values=['Age','Num_of_Delayed_Payment', 'Annual_Income', 'Monthly_Inhand_Salary', 'Num_Bank_Accounts',
                        'Num_Credit_Card', 'Num_of_Loan', 'Delay_from_due_date', 'Monthly_Balance', 'Outstanding_Debt'], 
               index='Credit_Score', 
               aggfunc=['mean'], dropna=True)

mean                                                    \
                    Age Annual_Income Delay_from_due_date Monthly_Balance   
Credit_Score                                                                
Good          36.335847  67719.599887           11.182715      497.194863   
Poor          31.034165  41953.411594           29.014349      349.396031   
Standard      32.994436  50611.427182           20.113392      409.091510   

                                                                      \
             Monthly_Inhand_Salary Num_Bank_Accounts Num_Credit_Card   
Credit_Score                                                           
Good                   5664.242492          3.441415        4.171694   
Poor                   3529.789908          6.330031        6.499146   
Standard               4261.364155          5.336723        5.362049   

                                                                  
             Num_of_Delayed_Payment Num_of_Loan Outstanding_Debt  
Credit_Score                                                      
Good                       8.216357    2.130510       757.737668  
Poor                      15.197472    4.687735      2012.966467  
Standard                  13.362817    3.298542      1277.661782

In [36]:
moda = lambda x: x.value_counts().values[0]

df.pivot_table(values=['Age','Num_of_Delayed_Payment', 'Annual_Income', 'Monthly_Inhand_Salary', 'Num_Bank_Accounts',
                        'Num_Credit_Card', 'Num_of_Loan', 'Delay_from_due_date', 'Monthly_Balance', 'Outstanding_Debt'], 
               index='Credit_Score', 
               aggfunc=[moda], dropna=True)

<lambda>                                                    \
                  Age Annual_Income Delay_from_due_date Monthly_Balance   
Credit_Score                                                              
Good               69            12                 136               1   
Poor              145            20                 105               1   
Standard          191            54                 203               1   

                                                                      \
             Monthly_Inhand_Salary Num_Bank_Accounts Num_Credit_Card   
Credit_Score                                                           
Good                             8               282             345   
Poor                             8               526             640   
Standard                         8               827            1052   

                                                                  
             Num_of_Delayed_Payment Num_of_Loan Outstanding_Debt  
Credit_Score                                                      
Good                            136         374                9  
Poor                            244         422                8  
Standard                        400         883               13

In [37]:
credit_score_categories = ['Poor', 'Standard', 'Good']

for category in credit_score_categories:
    filtered_df = df[df['Credit_Score'] == category]
    
    sns.kdeplot(filtered_df['Annual_Income'], label=category, shade=True)
    
    plt.axvline(x=filtered_df['Annual_Income'].mean(), linestyle='--', color='red', label='mean')
    plt.axvline(x=filtered_df['Annual_Income'].median(), linestyle='--', color='green', label='median')
    plt.axvline(x=filtered_df['Annual_Income'].mode()[0], linestyle='--', color='purple', label='mode')
    
    plt.title(f'Annual Income Distribution for Credit Score {category} Category')
    plt.xlabel('Annual Income')
    plt.ylabel('Density')
    plt.legend()

    plt.show()

In [38]:
for category in credit_score_categories:
    filtered_df = df[df['Credit_Score'] == category]
    
    plt.figure(figsize=(8, 3), dpi=80)
    sns.kdeplot(filtered_df['Delay_from_due_date'], label=category, shade=True)
    
    plt.axvline(x=filtered_df['Delay_from_due_date'].mean(), linestyle='--', color='red', label='mean')
    plt.axvline(x=filtered_df['Delay_from_due_date'].median(), linestyle='--', color='green', label='median')
    plt.axvline(x=filtered_df['Delay_from_due_date'].mode()[0], linestyle='--', color='purple', label='mode')
    
    plt.title(f'Delay_from_due_date Distribution for Credit Score {category} Category')
    plt.xlabel('Delay_from_due_date')
    plt.ylabel('Density')
    plt.legend()
    
    plt.show()

In [39]:
for category in credit_score_categories:
    filtered_df = df[df['Credit_Score'] == category]
    
    plt.figure(figsize=(8, 3), dpi=80)
    sns.kdeplot(filtered_df['Num_of_Loan'], label=category, shade=True)
    
    plt.axvline(x=filtered_df['Num_of_Loan'].mean(), linestyle='--', color='red', label='mean')
    plt.axvline(x=filtered_df['Num_of_Loan'].median(), linestyle='--', color='green', label='median')
    plt.axvline(x=filtered_df['Num_of_Loan'].mode()[0], linestyle='--', color='purple', label='mode')
    
    plt.title(f'Num_of_Loan Distribution for Credit Score {category} Category')
    plt.xlabel('Num_of_Loan')
    plt.ylabel('Density')
    plt.legend()
    
    plt.show()

In [40]:
df['Debt_Ratio'] = df['Outstanding_Debt'] / df['Monthly_Inhand_Salary']

df['Savings_Ratio'] = df['Monthly_Balance'] / df['Monthly_Inhand_Salary']

df['Credit_Utilization_Ratio'] = df['Num_of_Loan'] / df['Num_Credit_Card']

df['Payment_to_Income_Ratio'] = df['Delay_from_due_date'] / df['Monthly_Inhand_Salary']

In [41]:
df

Customer_ID             Name   Age  Occupation  Num_of_Delayed_Payment  \
0      CUS_0xd40    Aaron Maashoh  23.0   Scientist                     7.0   
1      CUS_0xd40    Aaron Maashoh  23.0   Scientist                     7.0   
2     CUS_0x21b1  Rick Rothackerj  28.0     Teacher                     1.0   
3     CUS_0x21b1  Rick Rothackerj  28.0     Teacher                     1.0   
4     CUS_0x21b1  Rick Rothackerj  28.0     Teacher                     1.0   
...          ...              ...   ...         ...                     ...   
9995  CUS_0xa1bd           Ermanv  41.0  Journalist                    12.0   
9996  CUS_0xa1bd           Ermanv  41.0  Journalist                    12.0   
9997  CUS_0xa1bd           Ermanv  41.0  Journalist                    12.0   
9998  CUS_0xa1bd           Ermanv  41.0  Journalist                    12.0   
9999  CUS_0xa1bd           Ermanv  41.0  Journalist                    12.0   

      Annual_Income  Monthly_Inhand_Salary  Num_Bank_Accounts  \
0          19114.12            1824.843333                  3   
1          19114.12            1824.843333                  3   
2          34847.84            3037.986667                  2   
3          34847.84            3037.986667                  2   
4          34847.84            3037.986667                  2   
...             ...                    ...                ...   
9995       23437.79            1711.149167                  8   
9996       23437.79            1711.149167                  8   
9997       23437.79            1711.149167                  8   
9998       23437.79            1711.149167                  8   
9999       23437.79            1711.149167                  8   

      Num_Credit_Card  Num_of_Loan  Delay_from_due_date  Monthly_Balance  \
0                   4            4                    3       312.494089   
1                   4            4                    3       244.565317   
2                   4            1                    3       470.690627   
3                   4            1                    7       484.591214   
4                   4            1                    3       466.466476   
...               ...          ...                  ...              ...   
9995                4            3                   24       320.619403   
9996                4            3                   25       328.626288   
9997                4            3                   25       328.717424   
9998                4            3                   24       244.964794   
9999                4            3                   25       240.272208   

      Outstanding_Debt Credit_Score  Credit_Score_Num  Debt_Ratio  \
0               809.98         Good                 2    0.443863   
1               809.98         Good                 2    0.443863   
2               605.03     Standard                 1    0.199155   
3               605.03         Good                 2    0.199155   
4               605.03     Standard                 1    0.199155   
...                ...          ...               ...         ...   
9995            589.94     Standard                 1    0.344762   
9996            589.94         Poor                 0    0.344762   
9997            589.94         Poor                 0    0.344762   
9998            589.94         Poor                 0    0.344762   
9999            589.94         Poor                 0    0.344762   

      Savings_Ratio  Credit_Utilization_Ratio  Payment_to_Income_Ratio  
0          0.171244                      1.00                 0.001644  
1          0.134020                      1.00                 0.001644  
2          0.154935                      0.25                 0.000987  
3          0.159511                      0.25                 0.002304  
4          0.153545                      0.25                 0.000987  
...             ...                       ...                      ...  
9995       0.187371   

In [42]:
for category in credit_score_categories:
    filtered_df = df[df['Credit_Score'] == category]

    plt.figure(figsize=(8, 3), dpi=80)
    sns.kdeplot(filtered_df['Debt_Ratio'], label=category, shade=True)
    
    plt.axvline(x=filtered_df['Debt_Ratio'].mean(), linestyle='--', color='red', label='mean')
    plt.axvline(x=filtered_df['Debt_Ratio'].median(), linestyle='--', color='green', label='median')
    plt.axvline(x=filtered_df['Debt_Ratio'].mode()[0], linestyle='--', color='purple', label='mode')
    
    plt.title(f'Debt_Ratio Distribution for Credit Score {category} Category')
    plt.xlabel('Debt_Ratio')
    plt.ylabel('Density')
    plt.legend()
    
    plt.show()

In [43]:

for category in credit_score_categories:
    filtered_df = df[df['Credit_Score'] == category]
    
    plt.figure(figsize=(8, 3), dpi=80)
    sns.kdeplot(filtered_df['Payment_to_Income_Ratio'], label=category, shade=True)
    
    plt.axvline(x=filtered_df['Payment_to_Income_Ratio'].mean(), linestyle='--', color='red', label='mean')
    plt.axvline(x=filtered_df['Payment_to_Income_Ratio'].median(), linestyle='--', color='green', label='median')
    plt.axvline(x=filtered_df['Payment_to_Income_Ratio'].mode()[0], linestyle='--', color='purple', label='mode')
    
    plt.title(f'Payment_to_Income_Ratio Distribution for Credit Score {category} Category')
    plt.xlabel('Payment_to_Income_Ratio')
    plt.ylabel('Density')
    plt.legend()
    
    plt.show()

# Подсчет количества добавленных признаков

In [44]:
print(f"Кол-во признаков в начале: {len(columns_start)}\nКол-во признаков сейчас: {len(df.columns)}\nНовые колонки: {', '.join(list(filter(lambda x: x not in columns_start, df.columns)))}")

Кол-во признаков в начале: 14
Кол-во признаков сейчас: 19
Новые колонки: Credit_Score_Num, Debt_Ratio, Savings_Ratio, Credit_Utilization_Ratio, Payment_to_Income_Ratio


# Гипотезы

In [45]:
from scipy.stats import ttest_1samp
from scipy.stats import ttest_ind

Нулевая гипотеза: учителя преимущественно имеют хороший статус кредитного скоринга.

Альтернативная гипотеза: учителя преимущественно не имеют хороший статус кредитного скоринга.

In [46]:
def encode_target(val):
    if val.lower() == "good":
        return 2
    elif val.lower() == "poor":
        return 0
    else:
        return 1

In [47]:
df['Credit_Score'] = df['Credit_Score'].apply(encode_target, )

In [48]:
alpha = 0.05
target = 2

results = ttest_1samp(df.loc[df['Occupation'] == 'Teacher', 'Credit_Score'], target)
print(f'p-value: {results.pvalue}')

if results.pvalue < alpha:
    print('Отвергаем нулевую гипотезу')
else:
    print('Не получилось отвергнуть нулевую гипотезу')

p-value: 2.0430992111700103e-192
Отвергаем нулевую гипотезу


Нулевая гипотеза: люди младше 33 отдают кредиты хуже чем люди старше 33.

Альтернативная гипотеза: люди младше 33 отдают кредиты не хуже, чем люди старше 33.

In [49]:
young_slice = df.loc[df['Age'] <= 33, 'Credit_Score']
old_slice = df.loc[df['Age'] > 33, 'Credit_Score']
results = ttest_ind(young_slice, old_slice)
print(f'p-value: {results.pvalue}')
if results.pvalue < alpha:
    print('Нулевя гипотеза отвергается')
else:
    print('Не удалось отвергнуть нулевую гипотезу')

p-value: 1.2473754738546628e-34
Нулевя гипотеза отвергается


# Обучение моделей

Решаем задачу многоклассовой классификации для кредитного скоринга, то есть параметр `credit_score`. Раздели выборку на обучающую, тестовую. 

In [50]:
RANDOM = 12345

In [51]:
from sklearn.model_selection import train_test_split
from sklearn import preprocessing
from sklearn.metrics import classification_report
from sklearn.preprocessing import OrdinalEncoder
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import StandardScaler

from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.linear_model import LogisticRegression
from xgboost import XGBClassifier
from sklearn.metrics import balanced_accuracy_score, accuracy_score

In [52]:
target = df['Credit_Score']
features = df.drop(['Credit_Score', 'Customer_ID', 'Name'], axis=1).fillna(0)

features_train, features_test, target_train, target_test = train_test_split(features, target, 
                                                                              test_size=0.15, random_state=RANDOM)
features_train, features_valid, target_train, target_valid = train_test_split(features_train, target_train, 
                                                                              test_size=0.25, random_state=RANDOM)

In [53]:
target.value_counts(normalize=True).plot(kind='bar')

<Axes: title={'center': 'Payment_to_Income_Ratio Distribution for Credit Score Good Category'}, xlabel='Payment_to_Income_Ratio', ylabel='Density'>

In [54]:
cat_features = ['Occupation']

ohe_encoder = OneHotEncoder(drop='first', sparse=False)

train_temp = ohe_encoder.fit_transform(features_train[cat_features])
features_train[ohe_encoder.get_feature_names_out()] = train_temp
features_train.drop(cat_features, axis=1, inplace=True)

valid_temp = ohe_encoder.transform(features_valid[cat_features])
features_valid[ohe_encoder.get_feature_names_out()] = valid_temp
features_valid.drop(cat_features, axis=1, inplace=True)

test_temp = ohe_encoder.transform(features_test[cat_features])
features_test[ohe_encoder.get_feature_names_out()] = test_temp
features_test.drop(cat_features, axis=1, inplace=True)

In [55]:
numeric = ['Age', 'Num_of_Delayed_Payment', 'Annual_Income',
       'Monthly_Inhand_Salary', 'Num_Bank_Accounts', 'Num_Credit_Card',
       'Num_of_Loan', 'Delay_from_due_date', 'Monthly_Balance',
       'Outstanding_Debt', 'Credit_Score_Num', 'Debt_Ratio', 'Savings_Ratio',
       'Credit_Utilization_Ratio', 'Payment_to_Income_Ratio',
       'Occupation_Architect', 'Occupation_Developer', 'Occupation_Doctor',
       'Occupation_Engineer', 'Occupation_Entrepreneur',
       'Occupation_Journalist', 'Occupation_Lawyer', 'Occupation_Manager',
       'Occupation_Mechanic', 'Occupation_Media_Manager',
       'Occupation_Musician', 'Occupation_Scientist', 'Occupation_Teacher',
       'Occupation_Writer']

scaler = StandardScaler()

features_train[numeric] = scaler.fit_transform(features_train[numeric])
features_valid[numeric] = scaler.fit_transform(features_valid[numeric])
features_test[numeric] = scaler.fit_transform(features_test[numeric])

## Проверка моделей

In [56]:
!python -m pip install xgboost

In [57]:
model_lr = LogisticRegression(random_state=RANDOM).fit(features_train, target_train)
preds_lr = model_lr.predict(features_valid)
probs_lr = model_lr.predict_proba(features_valid)

model_dt = DecisionTreeClassifier(random_state=RANDOM).fit(features_train, target_train)
preds_dt = model_dt.predict(features_valid)
probs_dt = model_dt.predict_proba(features_valid)

model_rf = RandomForestClassifier(random_state=RANDOM).fit(features_train, target_train)
preds_rf = model_rf.predict(features_valid)
probs_rf = model_rf.predict_proba(features_valid)

model_xg = XGBClassifier(random_state=RANDOM).fit(features_train, target_train)
preds_xg = model_xg.predict(features_valid)
probs_xg = model_xg.predict_proba(features_valid)

In [58]:
def count_metrics(preds, models, Y_test=target_valid):
    for index, model in enumerate(models):
        balanced_accuracy = balanced_accuracy_score(Y_test, preds[index])
        accuracy = accuracy_score(Y_test, preds[index])
        print(f"Accuracy/Balanced_accuracy for model {model} is {accuracy}/{balanced_accuracy}")
    
count_metrics(preds=[preds_lr, preds_dt, preds_rf, preds_xg], models=["LogReg", "DecisionTree", "RandomForest", "XGClf"])

Accuracy/Balanced_accuracy for model LogReg is 1.0/1.0
Accuracy/Balanced_accuracy for model DecisionTree is 1.0/1.0
Accuracy/Balanced_accuracy for model RandomForest is 0.9990458015267175/0.998095238095238
Accuracy/Balanced_accuracy for model XGClf is 1.0/1.0
